## Retail Strategy and Analytics

### Description
The projects uses Python to analyse the current purchasing trends and behaviours for a report that will help the company to understand the customer's purchasing behaviours and to develop a strategy to increase the customer's purchase. We will to derive features such as product, period, pack size and brand name from the data and define metrics of interest to draw insights on who spends on chips and what drives spends for each customer segment.

### Load required libraries and datasets

In [13]:
import time, os, string, json
import numpy as np
import pandas as pd

import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default = 'plotly_dark'
pio.renderers.default = 'notebook'
import datetime


In [5]:

df_customers = pd.read_csv('QVI_purchase_behaviour.csv')
df_customers


LYLTY_CARD_NBR               LIFESTAGE PREMIUM_CUSTOMER
0                1000   YOUNG SINGLES/COUPLES          Premium
1                1002   YOUNG SINGLES/COUPLES       Mainstream
2                1003          YOUNG FAMILIES           Budget
3                1004   OLDER SINGLES/COUPLES       Mainstream
4                1005  MIDAGE SINGLES/COUPLES       Mainstream
...               ...                     ...              ...
72632         2370651  MIDAGE SINGLES/COUPLES       Mainstream
72633         2370701          YOUNG FAMILIES       Mainstream
72634         2370751          YOUNG FAMILIES          Premium
72635         2370961          OLDER FAMILIES           Budget
72636         2373711   YOUNG SINGLES/COUPLES       Mainstream

[72637 rows x 3 columns]

In [6]:
# %%
df_transactions = pd.read_excel('QVI_transaction_data.xlsx')
df_transactions


DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0       43390          1            1000       1         5   
1       43599          1            1307     348        66   
2       43605          1            1343     383        61   
3       43329          2            2373     974        69   
4       43330          2            2426    1038       108   
...       ...        ...             ...     ...       ...   
264831  43533        272          272319  270088        89   
264832  43325        272          272358  270154        74   
264833  43410        272          272379  270187        51   
264834  43461        272          272379  270188        42   
264835  43365        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9  
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0  
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8  
...                                          ...       ...        ...  
264831   Kettle Sweet Chilli And Sour Cream 175g         2       10.8  
264832             Tostitos Splash Of  Lime 175g         1        4.4  
264833                  Doritos Mexicana    170g         2        8.8  
264834   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8  
264835             Tostitos Splash Of  Lime 175g         2        8.8  

[264836 rows x 8 columns]

### Exploratory data analysis
The first step in any analysis is to first understand the data. Let’s take a look at each of the datasets provided.

**Examining transaction data**
Let’s check if columns we would expect to be numeric are in numeric form and date columns are in dateformat.

In [7]:
# check types of columns in df_transactions
df_transactions.dtypes


DATE                int64
STORE_NBR           int64
LYLTY_CARD_NBR      int64
TXN_ID              int64
PROD_NBR            int64
PROD_NAME          object
PROD_QTY            int64
TOT_SALES         float64
dtype: object

We can see that the date column is in an integer format. Let’s change this to a date format.

In [8]:
# change the type of `DATE` column to datetime by adding it as the number of days since 1899-12-30
df_transactions['DATE'] = pd.to_datetime(df_transactions['DATE'], unit='D', origin='1899-12-30')
df_transactions.dtypes
df_transactions

DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0      2018-10-17          1            1000       1         5   
1      2019-05-14          1            1307     348        66   
2      2019-05-20          1            1343     383        61   
3      2018-08-17          2            2373     974        69   
4      2018-08-18          2            2426    1038       108   
...           ...        ...             ...     ...       ...   
264831 2019-03-09        272          272319  270088        89   
264832 2018-08-13        272          272358  270154        74   
264833 2018-11-06        272          272379  270187        51   
264834 2018-12-27        272          272379  270188        42   
264835 2018-09-22        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9  
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0  
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8  
...                                          ...       ...        ...  
264831   Kettle Sweet Chilli And Sour Cream 175g         2       10.8  
264832             Tostitos Splash Of  Lime 175g         1        4.4  
264833                  Doritos Mexicana    170g         2        8.8  
264834   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8  
264835             Tostitos Splash Of  Lime 175g         2        8.8  

[264836 rows x 8 columns]

Let's clean the null values in the dataset.

In [9]:
# check for NaN values in the df_transactions and delete the rows with NaN values
df_transactions.dropna(inplace=True)
df_transactions.isnull().sum()
df_transactions

DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0      2018-10-17          1            1000       1         5   
1      2019-05-14          1            1307     348        66   
2      2019-05-20          1            1343     383        61   
3      2018-08-17          2            2373     974        69   
4      2018-08-18          2            2426    1038       108   
...           ...        ...             ...     ...       ...   
264831 2019-03-09        272          272319  270088        89   
264832 2018-08-13        272          272358  270154        74   
264833 2018-11-06        272          272379  270187        51   
264834 2018-12-27        272          272379  270188        42   
264835 2018-09-22        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9  
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0  
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8  
...                                          ...       ...        ...  
264831   Kettle Sweet Chilli And Sour Cream 175g         2       10.8  
264832             Tostitos Splash Of  Lime 175g         1        4.4  
264833                  Doritos Mexicana    170g         2        8.8  
264834   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8  
264835             Tostitos Splash Of  Lime 175g         2        8.8  

[264836 rows x 8 columns]

Next, we should check that we are looking at the right products by examining PROD_NAME. Let’s remove all words with digits and special characters from our set of products

In [10]:
# examine the words in PROD_NAME to see if there are any incorrect entries amd remove the special characters and blank space from PROD_NAME
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace(r'[^\w\s]', '')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.strip()
df_transactions['PROD_NAME'].unique()
df_transactions

DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0      2018-10-17          1            1000       1         5   
1      2019-05-14          1            1307     348        66   
2      2019-05-20          1            1343     383        61   
3      2018-08-17          2            2373     974        69   
4      2018-08-18          2            2426    1038       108   
...           ...        ...             ...     ...       ...   
264831 2019-03-09        272          272319  270088        89   
264832 2018-08-13        272          272358  270154        74   
264833 2018-11-06        272          272379  270187        51   
264834 2018-12-27        272          272379  270188        42   
264835 2018-09-22        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9  
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0  
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8  
...                                          ...       ...        ...  
264831   Kettle Sweet Chilli And Sour Cream 175g         2       10.8  
264832             Tostitos Splash Of  Lime 175g         1        4.4  
264833                  Doritos Mexicana    170g         2        8.8  
264834   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8  
264835             Tostitos Splash Of  Lime 175g         2        8.8  

[264836 rows x 8 columns]

There are salsa products in the dataset but we are only interested in the chips category, so let’s remove

In [11]:
# Remove salsa products from PROD_NAME
df_transactions = df_transactions[~df_transactions['PROD_NAME'].str.contains('Salsa')]
df_transactions['PROD_NAME'].unique()
df_transactions

DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0      2018-10-17          1            1000       1         5   
1      2019-05-14          1            1307     348        66   
2      2019-05-20          1            1343     383        61   
3      2018-08-17          2            2373     974        69   
4      2018-08-18          2            2426    1038       108   
...           ...        ...             ...     ...       ...   
264831 2019-03-09        272          272319  270088        89   
264832 2018-08-13        272          272358  270154        74   
264833 2018-11-06        272          272379  270187        51   
264834 2018-12-27        272          272379  270188        42   
264835 2018-09-22        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9  
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0  
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8  
...                                          ...       ...        ...  
264831   Kettle Sweet Chilli And Sour Cream 175g         2       10.8  
264832             Tostitos Splash Of  Lime 175g         1        4.4  
264833                  Doritos Mexicana    170g         2        8.8  
264834   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8  
264835             Tostitos Splash Of  Lime 175g         2        8.8  

[246742 rows x 8 columns]

Next, we check summary statistics such as mean, min and max values for each feature to see if there are any obvious outliers in the data 

In [14]:
# plot the PROD_QTY column as a scatter plot with plotly express
fig = px.scatter(
    df_transactions,
    x='PROD_NBR',
    y='PROD_QTY',
    title='Scatter of PROD_NBR vs PROD_QTY',
)
fig

There appears to have an outlier which we should investigate further. Let’s investigate further the case where 200 packets of chips are bought in one transaction.


In [16]:
# show rows with PROD_QTY = 200
df_transactions[df_transactions['PROD_QTY'] == 200]


DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
69762 2018-08-19        226          226000  226201         4   
69763 2019-05-20        226          226000  226210         4   

                              PROD_NAME  PROD_QTY  TOT_SALES  
69762  Dorito Corn Chp     Supreme 380g       200      650.0  
69763  Dorito Corn Chp     Supreme 380g       200      650.0

There are two transactions where 200 packets of chips are bought in one transaction and both of these transactions where by the same customer.

In [17]:

# show all rows with LYLTY_CARD_NBR = 226000
df_transactions[df_transactions['LYLTY_CARD_NBR'] == 226000]


DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
69762 2018-08-19        226          226000  226201         4   
69763 2019-05-20        226          226000  226210         4   

                              PROD_NAME  PROD_QTY  TOT_SALES  
69762  Dorito Corn Chp     Supreme 380g       200      650.0  
69763  Dorito Corn Chp     Supreme 380g       200      650.0

It looks like this customer has only had the two transactions over the year and is not an ordinary retail customer. The customer might be buying chips for commercial purposes instead. We’ll remove this loyalty card number from further analysis

In [18]:

# delete the rows with PROD_QTY = 200 from the df_transactions dataframe
df_transactions = df_transactions[df_transactions['PROD_QTY'] != 200]
df_transactions


DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0      2018-10-17          1            1000       1         5   
1      2019-05-14          1            1307     348        66   
2      2019-05-20          1            1343     383        61   
3      2018-08-17          2            2373     974        69   
4      2018-08-18          2            2426    1038       108   
...           ...        ...             ...     ...       ...   
264831 2019-03-09        272          272319  270088        89   
264832 2018-08-13        272          272358  270154        74   
264833 2018-11-06        272          272379  270187        51   
264834 2018-12-27        272          272379  270188        42   
264835 2018-09-22        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9  
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0  
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8  
...                                          ...       ...        ...  
264831   Kettle Sweet Chilli And Sour Cream 175g         2       10.8  
264832             Tostitos Splash Of  Lime 175g         1        4.4  
264833                  Doritos Mexicana    170g         2        8.8  
264834   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8  
264835             Tostitos Splash Of  Lime 175g         2        8.8  

[246740 rows x 8 columns]

Now, let’s look at the number of transaction lines over time to see if there are any obvious data issues such as missing data.

In [19]:
# check for the number of transactions per date, and sort from earliest date to latest date
df_date_transactions = df_transactions.groupby('DATE').agg(
    count=('TXN_ID', 'count')
).sort_values('DATE').reset_index()
df_date_transactions


DATE  count
0   2018-07-01    663
1   2018-07-02    650
2   2018-07-03    674
3   2018-07-04    669
4   2018-07-05    660
..         ...    ...
359 2019-06-26    657
360 2019-06-27    669
361 2019-06-28    673
362 2019-06-29    703
363 2019-06-30    704

[364 rows x 2 columns]

There’s only 364 rows, meaning only 364 dates which indicates a missing date. Let’s create a sequence of dates from 1 Jul 2018 to 30 Jun 2019 and use this to create a chart of number of transactions over time to find the missing date.

In [20]:
# plot the number of transactions per date as a scatter chart with plotly express
fig = px.scatter(
    df_date_transactions,
    x='DATE',
    y='count',
    title='Number of Transactions per Date',
    labels={'count': 'Number of Transactions'}
)
fig

We can see that the increase in sales occurs in the lead-up to Christmas and that there are zero sales on Christmas day itself. This is due to shops being closed on Christmas day.

Now that we move on to creating other features as pack size from PROD_NAME. We will start with pack size.

In [21]:
# take the digits that are in PROD_NAME and convert them to intergers
df_pack_size = df_transactions['PROD_NAME'].str.extract(r'(\d+)').astype(int)
df_pack_size


0
0       175
1       175
2       170
3       175
4       150
...     ...
264831  175
264832  175
264833  170
264834  150
264835  175

[246740 rows x 1 columns]

In [22]:
# sort the pack size dataframe in descending order
df_pack_size = df_pack_size.sort_values(0, ascending=False).reset_index(drop=True)
df_pack_size

0
0       380
1       380
2       380
3       380
4       380
...     ...
246735   70
246736   70
246737   70
246738   70
246739   70

[246740 rows x 1 columns]

The largest size is 380g and the smallest size is 70g - seems sensible!

Let's plot a histogram of PACK_SIZE to see if any outliers

In [23]:
# plot the pack size as a histogram with plotly express
fig = px.histogram(
    df_pack_size,
    x=0,
    title='Histogram of Pack Size',
    labels={'0': 'Pack Size'}
)
fig


Pack sizes created look reasonable and now to create brands, we can use the first word in PROD_NAME to work out the brand name


In [24]:
# create a new dataframe which contains the first word of `PROD_NAME`
df_brand = df_transactions['PROD_NAME'].str.split().str[0]
df_brand


0          Natural
1              CCs
2           Smiths
3           Smiths
4           Kettle
            ...   
264831      Kettle
264832    Tostitos
264833     Doritos
264834     Doritos
264835    Tostitos
Name: PROD_NAME, Length: 246740, dtype: object

In [25]:
# count the number of unique values in df_brand
df_brand.value_counts()


PROD_NAME
Kettle        41288
Smiths        27390
Pringles      25102
Doritos       22041
Thins         14075
RRD           11894
Infuzions     11057
WW            10320
Cobs           9693
Tostitos       9471
Twisties       9454
Tyrrells       6442
Grain          6272
Natural        6050
Cheezels       4603
CCs            4551
Red            4427
Dorito         3183
Infzns         3144
Smith          2963
Cheetos        2927
Snbts          1576
Burger         1564
Woolworths     1516
GrnWves        1468
Sunbites       1432
NCC            1419
French         1418
Name: count, dtype: int64

Some of the brand names look like they are of the same brands - such as RED and RRD, which are both Red Rock Deli chips. Let’s combine these together.

In [27]:
# convert 'Red' to 'RRD' amd 'Dorito' to 'Doritos' and 'Infzns' to 'Infuzions' and 'WW' to 'Woolworths' and 'Smith' to 'Smiths' and 'Grain' to 'GrnWves' and 'Snbts' to 'Sunbites' and 'NCC' to 'Natural' in the `PROD_NAME` column of the df_transactions
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('Red', 'RRD')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('Doritos', 'Dorito')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('Infzns', 'Infuzions')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('WW', 'Woolworths')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('Smiths', 'Smiths')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('Grain', 'GrnWves')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('Snbts', 'Sunbites')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('NCC', 'Natural')
df_transactions['PROD_NAME'] = df_transactions['PROD_NAME'].str.replace('Dorito', 'Doritos')
df_transactions


C:\Users\BeBo\AppData\Local\Temp\ipykernel_5056\1719096412.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\BeBo\AppData\Local\Temp\ipykernel_5056\1719096412.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\BeBo\AppData\Local\Temp\ipykernel_5056\1719096412.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0      2018-10-17          1            1000       1         5   
1      2019-05-14          1            1307     348        66   
2      2019-05-20          1            1343     383        61   
3      2018-08-17          2            2373     974        69   
4      2018-08-18          2            2426    1038       108   
...           ...        ...             ...     ...       ...   
264831 2019-03-09        272          272319  270088        89   
264832 2018-08-13        272          272358  270154        74   
264833 2018-11-06        272          272379  270187        51   
264834 2018-12-27        272          272379  270188        42   
264835 2018-09-22        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  
0         Natural Chip        Compny SeaSalt175g         2        6.0  
1                       CCs Nacho Cheese    175g         3        6.3  
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9  
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0  
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8  
...                                          ...       ...        ...  
264831   Kettle Sweet Chilli And Sour Cream 175g         2       10.8  
264832             Tostitos Splash Of  Lime 175g         1        4.4  
264833                  Doritos Mexicana    170g         2        8.8  
264834   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8  
264835             Tostitos Splash Of  Lime 175g         2        8.8  

[246740 rows x 8 columns]

Let's check the dataset again

In [28]:
# check the uniques values in df_brand
df_brand = df_transactions['PROD_NAME'].str.split().str[0]
df_brand.value_counts()



PROD_NAME
Kettle        41288
Smiths        27390
Doritos       25224
Pringles      25102
RRD           16321
Infuzions     14201
Thins         14075
Woolworths    11836
Cobs           9693
Tostitos       9471
Twisties       9454
GrnWves        7740
Natural        7469
Tyrrells       6442
Cheezels       4603
CCs            4551
Sunbites       3008
Smith          2963
Cheetos        2927
Burger         1564
French         1418
Name: count, dtype: int64

Now that we are happy with the transaction dataset, let’s have a look at the customer dataset.

**Examining customer data**



In [29]:
# check the Nan values in the df_customers dataframe and delete the rows with Nan values
df_customers.dropna(inplace=True)
df_customers.isnull().sum()
df_customers


LYLTY_CARD_NBR               LIFESTAGE PREMIUM_CUSTOMER
0                1000   YOUNG SINGLES/COUPLES          Premium
1                1002   YOUNG SINGLES/COUPLES       Mainstream
2                1003          YOUNG FAMILIES           Budget
3                1004   OLDER SINGLES/COUPLES       Mainstream
4                1005  MIDAGE SINGLES/COUPLES       Mainstream
...               ...                     ...              ...
72632         2370651  MIDAGE SINGLES/COUPLES       Mainstream
72633         2370701          YOUNG FAMILIES       Mainstream
72634         2370751          YOUNG FAMILIES          Premium
72635         2370961          OLDER FAMILIES           Budget
72636         2373711   YOUNG SINGLES/COUPLES       Mainstream

[72637 rows x 3 columns]

In [21]:
# check the duplicates in the df_customers dataframe and delete the duplicates
df_customers.duplicated().sum()
df_customers.drop_duplicates(inplace=True)
df_customers.duplicated().sum()
df_customers


LYLTY_CARD_NBR               LIFESTAGE PREMIUM_CUSTOMER
0                1000   YOUNG SINGLES/COUPLES          Premium
1                1002   YOUNG SINGLES/COUPLES       Mainstream
2                1003          YOUNG FAMILIES           Budget
3                1004   OLDER SINGLES/COUPLES       Mainstream
4                1005  MIDAGE SINGLES/COUPLES       Mainstream
...               ...                     ...              ...
72632         2370651  MIDAGE SINGLES/COUPLES       Mainstream
72633         2370701          YOUNG FAMILIES       Mainstream
72634         2370751          YOUNG FAMILIES          Premium
72635         2370961          OLDER FAMILIES           Budget
72636         2373711   YOUNG SINGLES/COUPLES       Mainstream

[72637 rows x 3 columns]

Great, there are no nulls and duplcate values! So all our customers in the transaction data has been accounted for in the customer dataset.
Data exploration is now complete!


### Data analysis on customer segments
Now that the data is ready for analysis, we can define some metrics of interest to the client:
- Who spends the most on chips (total sales), describing customers by lifestage and how premium their general purchasing behaviour is
- How many customers are in each segment
- How many chips are bought per customer by segment
- What’s the average chip price by customer segment
Let’s start with calculating total sales by LIFESTAGE and PREMIUM_CUSTOMER


In [30]:
# merge the df_transactions and df_customers dataframes on the `LYLTY_CARD_NBR` column
df_merged = df_transactions.merge(df_customers, on='LYLTY_CARD_NBR')
df_merged


DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
0      2018-10-17          1            1000       1         5   
1      2019-05-14          1            1307     348        66   
2      2019-05-20          1            1343     383        61   
3      2018-08-17          2            2373     974        69   
4      2018-08-18          2            2426    1038       108   
...           ...        ...             ...     ...       ...   
246735 2019-03-09        272          272319  270088        89   
246736 2018-08-13        272          272358  270154        74   
246737 2018-11-06        272          272379  270187        51   
246738 2018-12-27        272          272379  270188        42   
246739 2018-09-22        272          272380  270189        74   

                                       PROD_NAME  PROD_QTY  TOT_SALES  \
0         Natural Chip        Compny SeaSalt175g         2        6.0   
1                       CCs Nacho Cheese    175g         3        6.3   
2         Smiths Crinkle Cut  Chips Chicken 170g         2        2.9   
3         Smiths Chip Thinly  S/Cream&Onion 175g         5       15.0   
4       Kettle Tortilla ChpsHny&Jlpno Chili 150g         3       13.8   
...                                          ...       ...        ...   
246735   Kettle Sweet Chilli And Sour Cream 175g         2       10.8   
246736             Tostitos Splash Of  Lime 175g         1        4.4   
246737                  Doritos Mexicana    170g         2        8.8   
246738   Doritos Corn Chip Mexican Jalapeno 150g         2        7.8   
246739             Tostitos Splash Of  Lime 175g         2        8.8   

                     LIFESTAGE PREMIUM_CUSTOMER  
0        YOUNG SINGLES/COUPLES          Premium  
1       MIDAGE SINGLES/COUPLES           Budget  
2       MIDAGE SINGLES/COUPLES           Budget  
3       MIDAGE SINGLES/COUPLES           Budget  
4       MIDAGE SINGLES/COUPLES           Budget  
...                        ...              ...  
246735   YOUNG SINGLES/COUPLES          Premium  
246736   YOUNG SINGLES/COUPLES          Premium  
246737   YOUNG SINGLES/COUPLES          Premium  
246738   YOUNG SINGLES/COUPLES          Premium  
246739   YOUNG SINGLES/COUPLES          Premium  

[246740 rows x 10 columns]

Now we plot the split by these segments to describe which customer segment contribute most to chip sales

In [31]:
# count percentage 'TOT_SALES' group by 'LIFESTAGE' and 'PREMIUM_CUSTOMER'
df_sales = df_merged.groupby(['LIFESTAGE', 'PREMIUM_CUSTOMER']).agg(
    total_sales=('TOT_SALES', 'sum')
).sort_values('total_sales', ascending=False).reset_index()
df_sales['total_sales_percentage'] = df_sales.groupby('LIFESTAGE')['total_sales'].transform(lambda x: x / x.sum() * 100)
df_sales


LIFESTAGE PREMIUM_CUSTOMER  total_sales  \
0           OLDER FAMILIES           Budget    156863.75   
1    YOUNG SINGLES/COUPLES       Mainstream    147582.20   
2                 RETIREES       Mainstream    145168.95   
3           YOUNG FAMILIES           Budget    129717.95   
4    OLDER SINGLES/COUPLES           Budget    127833.60   
5    OLDER SINGLES/COUPLES       Mainstream    124648.50   
6    OLDER SINGLES/COUPLES          Premium    123537.55   
7                 RETIREES           Budget    105916.30   
8           OLDER FAMILIES       Mainstream     96413.55   
9                 RETIREES          Premium     91296.65   
10          YOUNG FAMILIES       Mainstream     86338.25   
11  MIDAGE SINGLES/COUPLES       Mainstream     84734.25   
12          YOUNG FAMILIES          Premium     78571.70   
13          OLDER FAMILIES          Premium     75242.60   
14   YOUNG SINGLES/COUPLES           Budget     57122.10   
15  MIDAGE SINGLES/COUPLES          Premium     54443.85   
16   YOUNG SINGLES/COUPLES          Premium     39052.30   
17  MIDAGE SINGLES/COUPLES           Budget     33345.70   
18            NEW FAMILIES           Budget     20607.45   
19            NEW FAMILIES       Mainstream     15979.70   
20            NEW FAMILIES          Premium     10760.80   

    total_sales_percentage  
0                47.748630  
1                60.544904  
2                42.399715  
3                44.027721  
4                33.996521  
5                33.149464  
6                32.854014  
7                30.935134  
8                29.347857  
9                26.665151  
10               29.304166  
11               49.114528  
12               26.668113  
13               22.903514  
14               23.434073  
15               31.557298  
16               16.021023  
17               19.328174  
18               43.523426  
19               33.749508  
20               22.727066

In [32]:
# plot the chart in stacked bar with percenrage of total sales
fig = px.bar(
    df_sales,
    x='LIFESTAGE',
    y='total_sales_percentage',
    color='PREMIUM_CUSTOMER',
    title='Total Sales group by LIFESTAGE and PREMIUM_CUSTOMER',
    labels={'total_sales_percentage': 'Total Sales Percentage'},
    text_auto='.3s'
)
fig

Sales are coming mainly from Budget - older families, Mainstream - young singles/couples, and Mainstream - Retirees. And most loyal customer segments by lifestage are Mainsream young singles/couples, Mainstream Midage singles/couples, and Budget older families.

Let’s see if the higher sales are due to there being more customers who buy chips

In [23]:
# count the number of customers group by 'LIFESTAGE' and 'PREMIUM_CUSTOMER'
df_cus_count = df_merged.groupby(['LIFESTAGE', 'PREMIUM_CUSTOMER']).agg(
    count=('LYLTY_CARD_NBR', 'count')
).sort_values('count', ascending=False).reset_index()
df_cus_count 


LIFESTAGE PREMIUM_CUSTOMER  count
0           OLDER FAMILIES           Budget  21514
1                 RETIREES       Mainstream  19970
2    YOUNG SINGLES/COUPLES       Mainstream  19544
3           YOUNG FAMILIES           Budget  17763
4    OLDER SINGLES/COUPLES           Budget  17172
5    OLDER SINGLES/COUPLES       Mainstream  17061
6    OLDER SINGLES/COUPLES          Premium  16560
7                 RETIREES           Budget  14225
8           OLDER FAMILIES       Mainstream  13241
9                 RETIREES          Premium  12236
10          YOUNG FAMILIES       Mainstream  11947
11  MIDAGE SINGLES/COUPLES       Mainstream  11095
12          YOUNG FAMILIES          Premium  10784
13          OLDER FAMILIES          Premium  10403
14   YOUNG SINGLES/COUPLES           Budget   8573
15  MIDAGE SINGLES/COUPLES          Premium   7612
16   YOUNG SINGLES/COUPLES          Premium   5852
17  MIDAGE SINGLES/COUPLES           Budget   4691
18            NEW FAMILIES           Budget   2824
19            NEW FAMILIES       Mainstream   2185
20            NEW FAMILIES          Premium   1488

In [33]:
#count the proportion of customers group by 'LIFESTAGE' and 'PREMIUM_CUSTOMER'
df_cus_count['count_percentage'] = df_cus_count.groupby('LIFESTAGE')['count'].transform(lambda x: x / x.sum() * 100)
df_cus_count

NameError: name 'df_cus_count' is not defined

In [27]:
# plot the chart in stacked bar with percenrage of total customers
fig = px.bar(
    df_cus_count,
    x='LIFESTAGE',
    y='count_percentage',
    color='PREMIUM_CUSTOMER',
    title='Total Customers group by LIFESTAGE and PREMIUM_CUSTOMER',
    labels={'count_percentage': 'Total Customers Percentage'},
    text_auto='.3s'
)
fig

The mains cutomer segments generated for sales are Mainstream young singles/couples, Mainstream midage singles/couples, and Budget older families. And most loyal customer segments by lifestage are Mainstream young singles/couples, Mainstream midage singles/couples, and Budget older families.

Higher sales may also be driven by more units of chips being bought per customer. Let’s have a look at this next.

In [34]:
# count the number of units per customer by LIFESTAGE and PREMIUM_CUSTOMER by dividing the total quantity of products purchased by the number of customers
df_units_per_cus = df_merged.groupby(['LIFESTAGE', 'PREMIUM_CUSTOMER']).agg(
    total_units=('PROD_QTY', 'sum'),
    total_cus=('LYLTY_CARD_NBR', 'nunique')
).reset_index()
df_units_per_cus['units_per_cus'] = df_units_per_cus['total_units'] / df_units_per_cus['total_cus']
df_units_per_cus


LIFESTAGE PREMIUM_CUSTOMER  total_units  total_cus  \
0   MIDAGE SINGLES/COUPLES           Budget         8883       1474   
1   MIDAGE SINGLES/COUPLES       Mainstream        21213       3298   
2   MIDAGE SINGLES/COUPLES          Premium        14400       2369   
3             NEW FAMILIES           Budget         5241       1087   
4             NEW FAMILIES       Mainstream         4060        830   
5             NEW FAMILIES          Premium         2769        575   
6           OLDER FAMILIES           Budget        41853       4611   
7           OLDER FAMILIES       Mainstream        25804       2788   
8           OLDER FAMILIES          Premium        20239       2231   
9    OLDER SINGLES/COUPLES           Budget        32883       4849   
10   OLDER SINGLES/COUPLES       Mainstream        32607       4858   
11   OLDER SINGLES/COUPLES          Premium        31695       4682   
12                RETIREES           Budget        26932       4385   
13                RETIREES       Mainstream        37677       6358   
14                RETIREES          Premium        23266       3812   
15          YOUNG FAMILIES           Budget        34482       3953   
16          YOUNG FAMILIES       Mainstream        23194       2685   
17          YOUNG FAMILIES          Premium        20901       2398   
18   YOUNG SINGLES/COUPLES           Budget        15500       3647   
19   YOUNG SINGLES/COUPLES       Mainstream        36225       7917   
20   YOUNG SINGLES/COUPLES          Premium        10575       2480   

    units_per_cus  
0        6.026459  
1        6.432080  
2        6.078514  
3        4.821527  
4        4.891566  
5        4.815652  
6        9.076773  
7        9.255380  
8        9.071717  
9        6.781398  
10       6.712021  
11       6.769543  
12       6.141847  
13       5.925920  
14       6.103358  
15       8.722995  
16       8.638361  
17       8.716013  
18       4.250069  
19       4.575597  
20       4.264113

In [35]:

# plot df_units_per_cus as a group bar chart with plotly express
fig = px.bar(
    df_units_per_cus,
    x='LIFESTAGE',
    y='units_per_cus',
    color='PREMIUM_CUSTOMER',
    title='Units per Customer by LIFESTAGE and PREMIUM_CUSTOMER',
    labels={'units_per_cus': 'Units per Customer'},
    barmode='group',
)
fig


Older families and young families in general buy more chips per customer. 

 Let’s also investigate the average price per unit chips bought for each customer segment as this is also a driver of total sales.


In [36]:
# count the average price per unit by LIFESTAGE and PREMIUM_CUSTOMER by dividing the total sales by the total quantity of products purchased by each group
df_avg_price_per_unit = df_merged.groupby(['LIFESTAGE', 'PREMIUM_CUSTOMER']).agg(
    total_sales=('TOT_SALES', 'sum'),
    total_units=('PROD_QTY', 'sum')
).reset_index()
df_avg_price_per_unit['avg_price_per_unit'] = df_avg_price_per_unit['total_sales'] / df_avg_price_per_unit['total_units']
df_avg_price_per_unit


LIFESTAGE PREMIUM_CUSTOMER  total_sales  total_units  \
0   MIDAGE SINGLES/COUPLES           Budget     33345.70         8883   
1   MIDAGE SINGLES/COUPLES       Mainstream     84734.25        21213   
2   MIDAGE SINGLES/COUPLES          Premium     54443.85        14400   
3             NEW FAMILIES           Budget     20607.45         5241   
4             NEW FAMILIES       Mainstream     15979.70         4060   
5             NEW FAMILIES          Premium     10760.80         2769   
6           OLDER FAMILIES           Budget    156863.75        41853   
7           OLDER FAMILIES       Mainstream     96413.55        25804   
8           OLDER FAMILIES          Premium     75242.60        20239   
9    OLDER SINGLES/COUPLES           Budget    127833.60        32883   
10   OLDER SINGLES/COUPLES       Mainstream    124648.50        32607   
11   OLDER SINGLES/COUPLES          Premium    123537.55        31695   
12                RETIREES           Budget    105916.30        26932   
13                RETIREES       Mainstream    145168.95        37677   
14                RETIREES          Premium     91296.65        23266   
15          YOUNG FAMILIES           Budget    129717.95        34482   
16          YOUNG FAMILIES       Mainstream     86338.25        23194   
17          YOUNG FAMILIES          Premium     78571.70        20901   
18   YOUNG SINGLES/COUPLES           Budget     57122.10        15500   
19   YOUNG SINGLES/COUPLES       Mainstream    147582.20        36225   
20   YOUNG SINGLES/COUPLES          Premium     39052.30        10575   

    avg_price_per_unit  
0             3.753878  
1             3.994449  
2             3.780823  
3             3.931969  
4             3.935887  
5             3.886168  
6             3.747969  
7             3.736380  
8             3.717703  
9             3.887529  
10            3.822753  
11            3.897698  
12            3.932731  
13            3.852986  
14            3.924037  
15            3.761903  
16            3.722439  
17            3.759232  
18            3.685297  
19            4.074043  
20            3.692889

In [29]:
# plot df_avg_price_per_unit as a group bar chart with plotly express
fig = px.bar(
    df_avg_price_per_unit,
    x='LIFESTAGE',
    y='avg_price_per_unit',
    color='PREMIUM_CUSTOMER',
    title='Average Price per Unit by LIFESTAGE and PREMIUM_CUSTOMER',
    labels={'avg_price_per_unit': 'Average Price per Unit'},
    barmode='group',
)
fig

Mainstream midage and young singles and couples are more willing to pay more per packet of chips compared to their budget and premium counterparts. This may be due to premium shoppers being more likely to buy healthy snacks and when they buy chips, this is mainly for entertainment purposes rather than their own consumption. This is also supported by there being fewer premium midage and young singles and couples buying chips compared to their mainstream counterparts.

**Deep dive into specific customer segments for insights**
We will target customer segments that contribute the most to sales to retain them or further increase sales. Let’s look at Mainstream - young singles/couples

In [37]:
# create a new dataframe with columns of "Young Singles/Couples" and "Mainstream" from the df_merged dataframe
df_segment = df_merged[(df_merged['LIFESTAGE'] == 'YOUNG SINGLES/COUPLES') & (df_merged['PREMIUM_CUSTOMER'] == 'Mainstream')]
df_segment


DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
221345 2018-08-16          1            1020      26        19   
221346 2018-08-17          1            1163     188        46   
221347 2018-08-14          1            1291     333        27   
221348 2019-05-15          3            3031    1227        14   
221349 2019-05-18          3            3118    1574        62   
...           ...        ...             ...     ...       ...   
240884 2018-12-01        272          272377  270186        75   
240885 2018-07-27        272          272389  270200       114   
240886 2018-11-10        272          272389  270201        26   
240887 2019-04-01        272          272389  270202        62   
240888 2018-12-07        272          272391  270205        63   

                                          PROD_NAME  PROD_QTY  TOT_SALES  \
221345          Smiths Crinkle Cut  Snag&Sauce 150g         1        2.6   
221346                         Kettle Original 175g         1        5.4   
221347  Woolworths Supreme Cheese   Corn Chips 200g         1        1.9   
221348       Smiths Crnkle Chip  Orgnl Big Bag 380g         1        5.9   
221349             Pringles Mystery    Flavour 134g         1        3.7   
...                                             ...       ...        ...   
240884               Cobs Popd Sea Salt  Chips 110g         2        7.6   
240885        Kettle Sensations   Siracha Lime 150g         2        9.2   
240886                 Pringles Sweet&Spcy BBQ 134g         2        7.4   
240887             Pringles Mystery    Flavour 134g         2        7.4   
240888                 Kettle 135g Swt Pot Sea Salt         2        8.4   

                    LIFESTAGE PREMIUM_CUSTOMER  
221345  YOUNG SINGLES/COUPLES       Mainstream  
221346  YOUNG SINGLES/COUPLES       Mainstream  
221347  YOUNG SINGLES/COUPLES       Mainstream  
221348  YOUNG SINGLES/COUPLES       Mainstream  
221349  YOUNG SINGLES/COUPLES       Mainstream  
...                       ...              ...  
240884  YOUNG SINGLES/COUPLES       Mainstream  
240885  YOUNG SINGLES/COUPLES       Mainstream  
240886  YOUNG SINGLES/COUPLES       Mainstream  
240887  YOUNG SINGLES/COUPLES       Mainstream  
240888  YOUNG SINGLES/COUPLES       Mainstream  

[19544 rows x 10 columns]

In [40]:
# add a new column `BRAND` to the df_segment dataframe which contains the first word of `PROD_NAME`
df_segment['BRAND'] = df_segment['PROD_NAME'].str.split().str[0]
df_segment

C:\Users\BeBo\AppData\Local\Temp\ipykernel_5056\3506908064.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
221345 2018-08-16          1            1020      26        19   
221346 2018-08-17          1            1163     188        46   
221347 2018-08-14          1            1291     333        27   
221348 2019-05-15          3            3031    1227        14   
221349 2019-05-18          3            3118    1574        62   
...           ...        ...             ...     ...       ...   
240884 2018-12-01        272          272377  270186        75   
240885 2018-07-27        272          272389  270200       114   
240886 2018-11-10        272          272389  270201        26   
240887 2019-04-01        272          272389  270202        62   
240888 2018-12-07        272          272391  270205        63   

                                          PROD_NAME  PROD_QTY  TOT_SALES  \
221345          Smiths Crinkle Cut  Snag&Sauce 150g         1        2.6   
221346                         Kettle Original 175g         1        5.4   
221347  Woolworths Supreme Cheese   Corn Chips 200g         1        1.9   
221348       Smiths Crnkle Chip  Orgnl Big Bag 380g         1        5.9   
221349             Pringles Mystery    Flavour 134g         1        3.7   
...                                             ...       ...        ...   
240884               Cobs Popd Sea Salt  Chips 110g         2        7.6   
240885        Kettle Sensations   Siracha Lime 150g         2        9.2   
240886                 Pringles Sweet&Spcy BBQ 134g         2        7.4   
240887             Pringles Mystery    Flavour 134g         2        7.4   
240888                 Kettle 135g Swt Pot Sea Salt         2        8.4   

                    LIFESTAGE PREMIUM_CUSTOMER       BRAND  
221345  YOUNG SINGLES/COUPLES       Mainstream      Smiths  
221346  YOUNG SINGLES/COUPLES       Mainstream      Kettle  
221347  YOUNG SINGLES/COUPLES       Mainstream  Woolworths  
221348  YOUNG SINGLES/COUPLES       Mainstream      Smiths  
221349  YOUNG SINGLES/COUPLES       Mainstream    Pringles  
...                       ...              ...         ...  
240884  YOUNG SINGLES/COUPLES       Mainstream        Cobs  
240885  YOUNG SINGLES/COUPLES       Mainstream      Kettle  
240886  YOUNG SINGLES/COUPLES       Mainstream    Pringles  
240887  YOUNG SINGLES/COUPLES       Mainstream    Pringles  
240888  YOUNG SINGLES/COUPLES       Mainstream      Kettle  

[19544 rows x 11 columns]

In [41]:
# count the total sales group by 'BRAND' in the df_segment dataframe in descending order
df_brand_sales = df_segment.groupby('BRAND').agg(
    total_sales=('TOT_SALES', 'sum')
).sort_values('total_sales', ascending=False).reset_index()
df_brand_sales


BRAND  total_sales
0       Kettle      35423.6
1      Doritos      20925.9
2     Pringles      16006.2
3       Smiths      14337.5
4    Infuzions       8749.4
5     Twisties       7539.8
6     Tostitos       7238.0
7        Thins       7217.1
8         Cobs       6144.6
9     Tyrrells       4800.6
10         RRD       4509.9
11     GrnWves       4201.0
12    Cheezels       3318.3
13     Natural       2130.0
14  Woolworths       1605.8
15     Cheetos        898.8
16         CCs        850.5
17       Smith        621.4
18      French        429.0
19    Sunbites        391.0
20      Burger        243.8

In [42]:
# add the 'sale proportion' column to the df_brand_sales dataframe which contains the percentage of total sales of each brand
df_brand_sales['sale_proportion'] = df_brand_sales['total_sales'] / df_brand_sales['total_sales'].sum() * 100
df_brand_sales


BRAND  total_sales  sale_proportion
0       Kettle      35423.6        24.002624
1      Doritos      20925.9        14.179149
2     Pringles      16006.2        10.845617
3       Smiths      14337.5         9.714925
4    Infuzions       8749.4         5.928493
5     Twisties       7539.8         5.108882
6     Tostitos       7238.0         4.904385
7        Thins       7217.1         4.890224
8         Cobs       6144.6         4.163510
9     Tyrrells       4800.6         3.252831
10         RRD       4509.9         3.055856
11     GrnWves       4201.0         2.846549
12    Cheezels       3318.3         2.248442
13     Natural       2130.0         1.443263
14  Woolworths       1605.8         1.088072
15     Cheetos        898.8         0.609017
16         CCs        850.5         0.576289
17       Smith        621.4         0.421053
18      French        429.0         0.290685
19    Sunbites        391.0         0.264937
20      Burger        243.8         0.165196

We can see that the most favourite brands of Mainstream young singles/couples sre Kettel's, Doritos' and Pringles' while the least favourite are French's, Sunbites' and Burges's.

In [43]:
# plot the df_brand_sales as a pie chart with plotly express
fig = px.pie(
    df_brand_sales,
    values='total_sales',
    names='BRAND',
    title='Total Sales Proportion of Brands',
    labels={'total_sales': 'Total Sales'},
    hover_name='BRAND',
    hover_data={'sale_proportion': True},
)
fig


Next, we will look at the pack size preferences of Mainstream young singles/couples.

In [44]:
# add a new column `PACK_SIZE` to the df_segment dataframe which contains the digits in `PROD_NAME`
df_segment['PACK_SIZE'] = df_segment['PROD_NAME'].str.extract(r'(\d+)').astype(int)
df_segment

C:\Users\BeBo\AppData\Local\Temp\ipykernel_5056\3989890459.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



DATE  STORE_NBR  LYLTY_CARD_NBR  TXN_ID  PROD_NBR  \
221345 2018-08-16          1            1020      26        19   
221346 2018-08-17          1            1163     188        46   
221347 2018-08-14          1            1291     333        27   
221348 2019-05-15          3            3031    1227        14   
221349 2019-05-18          3            3118    1574        62   
...           ...        ...             ...     ...       ...   
240884 2018-12-01        272          272377  270186        75   
240885 2018-07-27        272          272389  270200       114   
240886 2018-11-10        272          272389  270201        26   
240887 2019-04-01        272          272389  270202        62   
240888 2018-12-07        272          272391  270205        63   

                                          PROD_NAME  PROD_QTY  TOT_SALES  \
221345          Smiths Crinkle Cut  Snag&Sauce 150g         1        2.6   
221346                         Kettle Original 175g         1        5.4   
221347  Woolworths Supreme Cheese   Corn Chips 200g         1        1.9   
221348       Smiths Crnkle Chip  Orgnl Big Bag 380g         1        5.9   
221349             Pringles Mystery    Flavour 134g         1        3.7   
...                                             ...       ...        ...   
240884               Cobs Popd Sea Salt  Chips 110g         2        7.6   
240885        Kettle Sensations   Siracha Lime 150g         2        9.2   
240886                 Pringles Sweet&Spcy BBQ 134g         2        7.4   
240887             Pringles Mystery    Flavour 134g         2        7.4   
240888                 Kettle 135g Swt Pot Sea Salt         2        8.4   

                    LIFESTAGE PREMIUM_CUSTOMER       BRAND  PACK_SIZE  
221345  YOUNG SINGLES/COUPLES       Mainstream      Smiths        150  
221346  YOUNG SINGLES/COUPLES       Mainstream      Kettle        175  
221347  YOUNG SINGLES/COUPLES       Mainstream  Woolworths        200  
221348  YOUNG SINGLES/COUPLES       Mainstream      Smiths        380  
221349  YOUNG SINGLES/COUPLES       Mainstream    Pringles        134  
...                       ...              ...         ...        ...  
240884  YOUNG SINGLES/COUPLES       Mainstream        Cobs        110  
240885  YOUNG SINGLES/COUPLES       Mainstream      Kettle        150  
240886  YOUNG SINGLES/COUPLES       Mainstream    Pringles        134  
240887  YOUNG SINGLES/COUPLES       Mainstream    Pringles        134  
240888  YOUNG SINGLES/COUPLES       Mainstream      Kettle        135  

[19544 rows x 12 columns]

In [45]:
# count the total sales group by 'PACK_SIZE' in the df_segment dataframe in descending order
df_pack_sales = df_segment.groupby('PACK_SIZE').agg(
    total_sales=('TOT_SALES', 'sum')
).sort_values('total_sales', ascending=False).reset_index()
df_pack_sales


PACK_SIZE  total_sales
0         175      37967.9
1         150      22946.2
2         134      16006.2
3         110      14630.0
4         330      12654.0
5         170      11893.4
6         165       7395.0
7         380       7175.9
8         270       5303.8
9         210       3798.0
10        135       2247.0
11        250       2236.0
12        190        739.8
13        200        617.5
14        160        440.8
15        180        403.0
16         90        391.0
17         70        264.0
18        220        243.8
19        125        228.9

In [46]:
# add the 'sale proportion' column to the df_pack_sales dataframe which contains the percentage of total sales of each pack size
df_pack_sales['sale_proportion'] = df_pack_sales['total_sales'] / df_pack_sales['total_sales'].sum() * 100
df_pack_sales


PACK_SIZE  total_sales  sale_proportion
0         175      37967.9        25.726612
1         150      22946.2        15.548081
2         134      16006.2        10.845617
3         110      14630.0         9.913120
4         330      12654.0         8.574205
5         170      11893.4         8.058831
6         165       7395.0         5.010767
7         380       7175.9         4.862307
8         270       5303.8         3.593794
9         210       3798.0         2.573481
10        135       2247.0         1.522541
11        250       2236.0         1.515088
12        190        739.8         0.501280
13        200        617.5         0.418411
14        160        440.8         0.298681
15        180        403.0         0.273068
16         90        391.0         0.264937
17         70        264.0         0.178883
18        220        243.8         0.165196
19        125        228.9         0.155100

In [47]:

# plot the df_pack_sales as a pie chart with plotly express
fig = px.pie(
    df_pack_sales,
    values='total_sales',
    names='PACK_SIZE',
    title='Total Sales Proportion of Pack Size',
    labels={'total_sales': 'Total Sales'},
    hover_name='PACK_SIZE',
    hover_data={'sale_proportion': True},
)
fig



We can see that the most favourite pack sizes of Mainstream young singles/couples are 175g and 150g while the least favourite are 125g and 220g.

### Conclusion
- Sales have mainly been due to Budget - older families, Mainstream - young singles/couples, and Mainstream - retirees shoppers. We found that the high spend in chips for mainstream young singles/couples and retirees is due to there being more of them than other buyers. Mainstream, midage and young singles and couples are also more likely to pay more per packet of chips. This is indicative of impulse buying behaviour.
- We’ve also found that Mainstream young singles and couples are more likely to purchase Kettel's and Doritos' and Pringles' chips compared to the rest of the brands. The recommendations are to increase the category’s performance by off-locating some Kettel's and Doritos' and Pringles' and in 150g/175g packs of chips in discretionary space near segments where young singles and couples frequent more often to increase visibilty and impulse behaviour.